In [2]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
import pandas as pd
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup
import re

In [3]:
# Khởi tạo trình duyệt Chrome
options = webdriver.ChromeOptions()
options.add_argument("--start-maximized") 
options.add_argument("--disable-blink-features=AutomationControlled")  
service = Service(ChromeDriverManager().install())
driver = webdriver.Chrome(service=service, options=options)

In [5]:
# Đọc file CSV đầu vào
input_csv = "D:/BaiDoAnChuyenNganh3/Automated-Resume-Ranking-System-main/csvfiles/crawlcv/crawldata3links.csv"  # Thay bằng tên file thực tế của bạn
df_input = pd.read_csv(input_csv)

In [6]:
# Danh sách để lưu dữ liệu crawl được
data = []

In [8]:
# Hàm định dạng lại văn bản cho đẹp (đặc biệt là số điện thoại, địa chỉ)
def format_text(text):
    # Loại bỏ khoảng trắng thừa
    text = re.sub(r'\s+', ' ', text).strip()
    
    # Định dạng số điện thoại (ví dụ: (555) 555-5555)
    phone_pattern = r'\(?\d{3}\)?\s*-?\s*\d{3}\s*-?\s*\d{4}'
    phone_matches = re.findall(phone_pattern, text)
    for phone in phone_matches:
        # Chuẩn hóa số điện thoại thành dạng (555) 555-5555
        phone_clean = re.sub(r'\D', '', phone)  # Loại bỏ ký tự không phải số
        formatted_phone = f"({phone_clean[:3]}) {phone_clean[3:6]}-{phone_clean[6:]}"
        text = text.replace(phone, formatted_phone)
    
    # Định dạng email (đảm bảo không có khoảng trắng thừa)
    email_pattern = r'[\w\.-]+@[\w\.-]+\.\w+'
    email_matches = re.findall(email_pattern, text)
    for email in email_matches:
        text = text.replace(email, email.strip())
    
    # Định dạng địa chỉ (thêm khoảng cách hợp lý)
    address_pattern = r'[A-Za-z\s]+,\s*[A-Za-z\s]+,\s*[A-Za-z\s]+,\s*\d{5}'
    address_matches = re.findall(address_pattern, text)
    for address in address_matches:
        formatted_address = address.replace(',', ', ')
        text = text.replace(address, formatted_address)
    
    # Thêm dòng mới giữa các đoạn
    text = re.sub(r'\n\s*\n+', '\n', text)  # Loại bỏ dòng trống thừa
    return text

# Duyệt qua từng link trong file CSV
for index, row in df_input.iterrows():
    resume_link = row['resume_link']
    category = row['Category']
    
    print(f"Đang crawl link: {resume_link}")
    
    try:
        # Truy cập link
        driver.get(resume_link)
        time.sleep(2)  # Chờ trang tải hoàn toàn
        
        # Biến để lưu nội dung
        resume_str = ""
        resume_html = ""
        
        # Kiểm tra dạng 1
        try:
            # Tìm section với class "jbt-txt-version"
            jbt_section = WebDriverWait(driver, 5).until(
                EC.presence_of_element_located((By.CLASS_NAME, "jbt-txt-version"))
            )
            
            # Tìm div class "jbt-container"
            jbt_container = jbt_section.find_element(By.CLASS_NAME, "jbt-container")
            
            # Tìm div class "text-only"
            text_only = jbt_container.find_element(By.CLASS_NAME, "text-only")
            
            # Lấy nội dung HTML của section (bao gồm tất cả thẻ con)
            resume_html = jbt_section.get_attribute('outerHTML')
            
            # Dùng BeautifulSoup để lấy nội dung văn bản từ các thẻ p, ul
            soup = BeautifulSoup(resume_html, 'html.parser')
            text_parts = []
            
            # Lấy tất cả các thẻ p
            for p_tag in soup.find_all('p'):
                text = p_tag.get_text(separator=" ", strip=True)
                if text:
                    text_parts.append(text)
            
            # Lấy tất cả các thẻ ul
            for ul_tag in soup.find_all('ul'):
                for li_tag in ul_tag.find_all('li'):
                    li_text = li_tag.get_text(separator=" ", strip=True)
                    if li_text:
                        text_parts.append(li_text)
            
            # Gộp nội dung thành resume_str
            resume_str = "\n".join(text_parts)
            resume_str = format_text(resume_str)
            
            print("Tìm thấy dạng 1: jbt-txt-version")
            
        except Exception as e:
            print(f"Không tìm thấy dạng 1: {e}")
            
            # Kiểm tra dạng 2
            try:
                # Tìm div với class "container-xs content-wbg p-tb-50 grey-bg txt-cv cta-center"
                container_xs = WebDriverWait(driver, 5).until(
                    EC.presence_of_element_located((By.CLASS_NAME, "container-xs.content-wbg.p-tb-50.grey-bg.txt-cv.cta-center"))
                )
                
                # Lấy nội dung HTML từ container-xs (bao gồm tất cả thẻ con)
                resume_html = container_xs.get_attribute('outerHTML')
                
                # Tìm div class "container"
                container = container_xs.find_element(By.CLASS_NAME, "container")
                
                # Tìm div class "editor-content"
                editor_content = container.find_element(By.CLASS_NAME, "editor-content")
                
                # Dùng BeautifulSoup để lấy nội dung văn bản từ các thẻ div, p, ul, li trong editor-content
                editor_html = editor_content.get_attribute('outerHTML')
                soup = BeautifulSoup(editor_html, 'html.parser')
                text_parts = []
                
                # Lấy tất cả các thẻ div
                for div_tag in soup.find_all('div'):
                    div_text = div_tag.get_text(separator=" ", strip=True)
                    if div_text:
                        text_parts.append(div_text)
                
                # Lấy tất cả các thẻ p
                for p_tag in soup.find_all('p'):
                    p_text = p_tag.get_text(separator=" ", strip=True)
                    if p_text:
                        text_parts.append(p_text)
                
                # Lấy tất cả các thẻ ul
                for ul_tag in soup.find_all('ul'):
                    for li_tag in ul_tag.find_all('li'):
                        li_text = li_tag.get_text(separator=" ", strip=True)
                        if li_text:
                            text_parts.append(li_text)
                
                # Gộp nội dung thành resume_str
                resume_str = "\n".join(text_parts)
                resume_str = format_text(resume_str)
                
                print("Tìm thấy dạng 2: container-xs content-wbg p-tb-50 grey-bg txt-cv cta-center")
                
            except Exception as e:
                print(f"Không tìm thấy dạng 2: {e}")
                print(f"Link {resume_link} không thuộc dạng 1 hoặc dạng 2.")
                continue
        
        # Thêm dữ liệu vào danh sách
        data.append({
            "ID": index + 1,  # Bắt đầu từ 1
            "resume_str": resume_str,
            "resume_html": resume_html,
            "Category": category
        })
        
    except Exception as e:
        print(f"Lỗi khi crawl link {resume_link}: {e}")
        continue

Đang crawl link: https://www.myperfectresume.com/cv/examples/accounting/trainee
Không tìm thấy dạng 1: Message: 
Stacktrace:
	GetHandleVerifier [0x00A08D03+51395]
	(No symbol) [0x00975F61]
	(No symbol) [0x0082E13A]
	(No symbol) [0x008662BB]
	(No symbol) [0x008663EB]
	(No symbol) [0x0089C162]
	(No symbol) [0x00883ED4]
	(No symbol) [0x0089A570]
	(No symbol) [0x00883C26]
	(No symbol) [0x0085C629]
	(No symbol) [0x0085D40D]
	GetHandleVerifier [0x00D868D3+3712147]
	GetHandleVerifier [0x00DC5CBA+3971194]
	GetHandleVerifier [0x00DC0FA8+3951464]
	GetHandleVerifier [0x00AB9D09+776393]
	(No symbol) [0x00981734]
	(No symbol) [0x0097C618]
	(No symbol) [0x0097C7C9]
	(No symbol) [0x0096DDF0]
	BaseThreadInitThunk [0x76A85D49+25]
	RtlInitializeExceptionChain [0x776DCE3B+107]
	RtlGetAppContainerNamedObjectPath [0x776DCDC1+561]

Tìm thấy dạng 2: container-xs content-wbg p-tb-50 grey-bg txt-cv cta-center
Đang crawl link: https://www.myperfectresume.com/cv/examples/accounting/officer
Không tìm thấy dạng 1:

In [12]:
# Loại bỏ các bản ghi trùng lặp dựa trên 'ID', giữ lại bản ghi cuối cùng
seen_ids = set()
unique_data = []

for record in reversed(data):  # Duyệt ngược để giữ bản ghi cuối cùng
    if record['ID'] not in seen_ids:
        seen_ids.add(record['ID'])
        unique_data.append(record)

# Đảo ngược lại để giữ thứ tự ban đầu
unique_data = unique_data[::-1]

In [13]:
# In dữ liệu theo dạng dọc để kiểm tra
print("Dữ liệu crawl được:")
for item in data:
    print(f"ID: {item['ID']}")
    print(f"resume_str:\n{item['resume_str']}")
    print(f"resume_html:\n{item['resume_html']}")
    print(f"Category: {item['Category']}")
    print("-" * 50)  # Dòng phân cách giữa các mục

Dữ liệu crawl được:
ID: 1
resume_str:
Heather Chambers 123 Fake Street, City, State, Zip Code E: email@email.com P: (000) 000-0000 Professional Summary Conscientious accountant trainee with two years of professional experience in an office setting. Assist accountants with preparing financial reports and maintaining financial records. Shadow accountants to learn best practices; quick learner with an eye for detail and a strong interest in the subject matter. Currently enrolled in last year of B.S. in accounting. Skills Understanding of Intuit QuickBooks, Sage 50 Accounting, Yardi Systems Yardi Enterprise, ATX Total Tax Office, and Oracle E-Business Suite Financials Thorough knowledge of statistics, algebra, geometry, calculus, and arithmetic Skilled in administrative procedures and systems, including managing records and files, word processing, and transcription and stenography Active listening and learning skills for comprehending job duties and asking questions when necessary Strong c

In [14]:
# Đóng trình duyệt
driver.quit()

In [15]:
# Chuyển dữ liệu thành DataFrame
df = pd.DataFrame(data)

In [ ]:
df.head(5)

In [17]:
# Loại bỏ các bản ghi trùng lặp dựa trên cột 'ID', giữ lại bản ghi cuối cùng
df = df.drop_duplicates(subset=['ID'], keep='last')

# In số lượng bản ghi sau khi loại bỏ trùng lặp
print(f"Số lượng bản ghi sau khi loại bỏ trùng lặp: {len(df)}")

# In dữ liệu để kiểm tra
print("Dữ liệu sau khi loại bỏ trùng lặp:")
print(df)

Số lượng bản ghi sau khi loại bỏ trùng lặp: 245
Dữ liệu sau khi loại bỏ trùng lặp:
      ID                                         resume_str  \
3      1  Heather Chambers 123 Fake Street, City, State,...   
4      2  Alexander Butler 123 Fake Street, City, State,...   
5      3  Jessica Francis 123 Fake Street, City, State, ...   
6      4  Brittany Finn 123 Fake Street, City, State, Zi...   
7      5  EMILY WALTERS Philadelphia, PA 19091 (555) 555...   
..   ...                                                ...   
243  241  Jennifer Ikeda 123 Fake Street, City, State, Z...   
244  242  Lizzie Carlson Hollywood, FL 33004 (555) 555-5...   
245  243  Evan Gillman Phoenix, AZ 85053 (555) 555-5555 ...   
246  244  Geena Meadows 123 Fake Street, City, State, Zi...   
247  245  Scott Wagner San Francisco, CA 94132 (555) 555...   

                                           resume_html  \
3    <div class="container-xs content-wbg p-tb-50 g...   
4    <div class="container-xs content-wbg p-

In [ ]:
# Lưu vào file CSV
output_file = "D:/BaiDoAnChuyenNganh3/Automated-Resume-Ranking-System-main/csvfiles/crawlcv/finaldata3links.csv"
df.to_csv(output_file, index=False, encoding="utf-8")
print(f"Dữ liệu đã được lưu vào file: {output_file}")
print(f"Tổng số link crawl được: {len(df)}")

Dữ liệu đã được lưu vào file: D:/BaiDoAnChuyenNganh3/Automated-Resume-Ranking-System-main/csvfiles/crawlcv/finaldata3links.csv
Tổng số link crawl được: 245


: 